In [23]:
%pip install llama-cpp-python


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Note: you may need to restart the kernel to use updated packages.


In [1]:
import json


with open('abstracts_to_categories.json', 'r') as file:
    data = json.load(file)


abstracts = list(data.keys())
categories = list(data.values())

print(abstracts)

category_list = []
for i in categories:
    for item in i:
        category_list.append(item)

print(category_list)


["The extant research sheds light on the vital role of co-creation in online healthcare communities (OHCs) as nascent peer-to-peer co-creation platforms in public health and well-being. However, more investigation of the underlying factors affecting patient value co-creation in OHCs is required. This study relies on the socio-technical theory to identify the social and technical factors that impact healthcare users' intention to co-create value. Analysis of survey data gathered from users of Top 10 healthcare-based pages on Facebook indicated that both social and technical factors are salient in the prediction of value co-creation in OHCs. More specifically, social support and its antecedents (i.e., perceived privacy risk and social media interactivity), as well as government IT infrastructures and perceived control of information, are found to be the critical antecedents of value co-creation intention. However, social support emerged as the most potent predictor of value co-creation r

In [18]:
from bertopic import BERTopic
from bertopic.representation import KeyBERTInspired
from sentence_transformers import SentenceTransformer

In [43]:
from bertopic import BERTopic
from bertopic.representation import LlamaCPP
from llama_cpp import Llama

# Use llama.cpp to load in a 4-bit quantized version of Zephyr 7B Alpha
#representation_model = LlamaCPP("zephyr-7b-alpha.Q4_K_M.gguf", n_gpu_layers=-1, n_ctx=4096, stop="Q:")
#llm = Llama(model_path="zephyr-7b-alpha.Q4_K_M.gguf", n_gpu_layers=-1, n_ctx=16000,n_batch=8000, stop="Q:")
#representation_model = LlamaCPP(llm)
# # Create our BERTopic model
# topic_model = BERTopic(representation_model=representation_model,  verbose=True)


llama_model_loader: loaded meta data with 21 key-value pairs and 291 tensors from zephyr-7b-alpha.Q4_K_M.gguf (version GGUF V2)
llama_model_loader: Dumping metadata keys/values. Note: KV overrides do not apply in this output.
llama_model_loader: - kv   0:                       general.architecture str              = llama
llama_model_loader: - kv   1:                               general.name str              = huggingfaceh4_zephyr-7b-alpha
llama_model_loader: - kv   2:                       llama.context_length u32              = 32768
llama_model_loader: - kv   3:                     llama.embedding_length u32              = 4096
llama_model_loader: - kv   4:                          llama.block_count u32              = 32
llama_model_loader: - kv   5:                  llama.feed_forward_length u32              = 14336
llama_model_loader: - kv   6:                 llama.rope.dimension_count u32              = 128
llama_model_loader: - kv   7:                 llama.attention.head_cou

In [63]:

# create the model, set the embedding model, and the similarity
topic_model = BERTopic(
    embedding_model="thenlper/gte-small",
    #embedding_model="all-MiniLM-L6-v2",
    min_topic_size=15,
    zeroshot_topic_list=category_list,
    zeroshot_min_similarity=.85,
    #representation_model=representation_model,
    representation_model=KeyBERTInspired(),
    verbose=True
)
topics, other = topic_model.fit_transform(abstracts)

2024-03-09 14:31:36,327 - BERTopic - Embedding - Transforming documents to embeddings.
Batches: 100%|██████████| 14/14 [00:12<00:00,  1.09it/s]
2024-03-09 14:31:51,014 - BERTopic - Embedding - Completed ✓
2024-03-09 14:31:51,014 - BERTopic - Zeroshot Step 1 - Finding documents that could be assigned to either one of the zero-shot topics
2024-03-09 14:31:51,362 - BERTopic - Zeroshot Step 1 - Completed ✓
2024-03-09 14:31:51,368 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-09 14:32:00,473 - BERTopic - Dimensionality - Completed ✓
2024-03-09 14:32:00,480 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-09 14:32:00,490 - BERTopic - Cluster - Completed ✓
2024-03-09 14:32:00,492 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-09 14:32:01,435 - BERTopic - Representation - Completed ✓
2024-03-09 14:32:01,489 - BERTopic - Zeroshot Step 2 - Clustering documents that were not found in t

In [83]:
table = topic_model.get_topic_info()
for i in table['Representative_Docs'][0]:
    print(i)
info_dict = {key: value for key, value in zip(table['Name'].tolist(), table['Representative_Docs'].tolist())}
print(len(info_dict.keys()))
print(len(info_dict.values()))

abstract_list: list[str] = []
abstract_set: set[str] = set()

count = 0
for key, values in info_dict.items():
    print(key)
    print(values)
    if count == 10:
        break
    #print(f"key: {key}\tvalue: {value}\n")
    for value in values:
        print(value)
        for v in value:
            print(v)
            abstract_list.append(value)
            abstract_set.add(value)
    count += 1
print(f"items in original abstract list: {len(abstracts)}")
print(f"Items in Abstract List: {len(abstract_list)}")
print(f"Items in Abstract Set: {len(abstract_set)}")

# go through all abstracts across all topics and add each topic's abstracts to a list
# attempt to do the same with a set
# since sets don't allow duplicates if at the end the number of abstracts 
# in the list is greater than the number of abstract in the set
# then it means abstracts got mapped to more than one topic

The Council on Social Work Education understands the growing influence of technology on social work practice and education, including the need for students to develop the knowledge and skills to use modern technologies, including Twitter, both professionally and ethically. With the inclusion of technology in social work education, the efficacy of these methods must be assessed. This study aims to conduct the initial phase of scale development, an exploratory factor analysis. Using a purposive sample of over 200 BSW and MSW students in one university, this study presents results of the exploratory phase of the Technology Effectiveness and Social Connectedness Scale, which can be used to assess the effectiveness of incorporating Twitter into social work courses.
Borders play a profound role in human life. In many settings, land borders are highly permeable and provide little barrier to movement, communication and interaction. In other circumstances, borders are highly rigid, difficult to

In [28]:
topic_model.get_topic(3)

[(' Retail Technology and Digital Payments for Entrepreneurial Firms and', 1),
 ('', 0),
 ('', 0),
 ('', 0),
 ('', 0),
 ('', 0),
 ('', 0),
 ('', 0),
 ('', 0),
 ('', 0)]

In [6]:
topic_distr, _ = topic_model.approximate_distribution(abstracts)

In [12]:
%pip install ipython

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Note: you may need to restart the kernel to use updated packages.


In [22]:
topic_model.visualize_distribution(topic_distr[0])

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'marker': {'color': '#C8D2D7', 'line': {'color': '#6E8484', 'width': 1}},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.04580621448688339, 0.06320379802753853, 0.38158140452290656,
                    0.019316371526748023, 0.021918079740289097, 0.0196901955694301,
                    0.02505408270642185, 0.043157531004373265, 0.05223357825986198,
                    0.021248416210154844, 0.12944381937058666, 0.03547129535739268,
                    0.0547196549184024, 0.016576114852463165],
              'y': [<b>Topic 1</b>: empathy_victimization_ps..., <b>Topic 12</b>:
                    practitioners_social_ar..., <b>Topic 17</b>:
                    ethics_ethical_moral_va..., <b>Topic 19</b>:
                    economics_economists_co..., <b>Topic 25</b>:
                    business_regulators_end..., <b>Topic 26</b>:
                    embodied_pain_conscious..., <b>Topic 32</b>:
                    entrepreneurship_busine..., <b>Topic 37</b>:
                    diplomacy_international..., <b>Topic 44</b>:
                    lobbying_environmentall..., <b>Topic 64</b>:
                    privilege_oppression_co..., <b>Topic 79</b>:
                    capitalistorganizations..., <b>Topic 86</b>:
                    libraries_health_facebo..., <b>Topic 100</b>:
                    turnover_china_retenti..., <b>Topic 127</b>:
                    humor_disabilities_men...]}],
    'layout': {'height': 600,
               'hoverlabel': {'bgcolor': 'white', 'font': {'family': 'Rockwell', 'size': 16}},
               'template': '...',
               'title': {'font': {'color': 'Black', 'size': 22},
                         'text': '<b>Topic Probability Distribution</b>',
                         'x': 0.5,
                         'xanchor': 'center',
                         'y': 0.95,
                         'yanchor': 'top'},
               'width': 800,
               'xaxis': {'title': {'text': 'Probability'}}}
})

In [19]:
topic_model.visualize_topics()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'customdata': array([[0, 'risk | resilience | risks | analytics | firms', 14],
                                   [1, 'empathy | victimization | psychological | rape | psychology', 13],
                                   [2, 'algebras | algebra | schubert | grassmannian | mathematics', 12],
                                   ...,
                                   [139, 'stiffness | exercises | exercise | resistance | cardiovascular',
                                    1],
                                   [140, 'turtles | turtle | sexes | wildlife | wetlands', 1],
                                   [141,
                                    'caterpillars | caterpillar | symplocaceae | species | hairstreak', 1]],
                                  dtype=object),
              'hovertemplate': '<b>Topic %{customdata[0]}</b><br>%{customdata[1]}<br>Size: %{customdata[2]}',
              'legendgroup': '',
              'marker': {'color': '#B0BEC5',
                         'line': {'color': 'DarkSlateGrey', 'width': 2},
                         'size': array([14, 13, 12, 12, 11, 11, 11,  9,  9,  9,  9,  8,  7,  7,  7,  7,  6,  6,
                                         6,  6,  6,  5,  5,  5,  5,  5,  5,  5,  4,  4,  4,  4,  4,  4,  4,  4,
                                         4,  4,  4,  4,  4,  4,  3,  3,  3,  3,  3,  3,  3,  3,  3,  3,  3,  3,
                                         3,  3,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,
                                         2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  2,  1,  1,  1,  1,  1,  1,  1,
                                         1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
                                         1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
                                         1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1]),
                         'sizemode': 'area',
                         'sizeref': 0.00875,
                         'symbol': 'circle'},
              'mode': 'markers',
              'name': '',
              'orientation': 'v',
              'showlegend': False,
              'type': 'scatter',
              'x': array([ 1.26580727e+00, -1.71165240e+00, -5.93564630e-01,  1.72494686e+00,
                           3.38917464e-01,  1.29382086e+00,  8.16569138e+00,  1.01822643e+01,
                           1.63753796e+01,  1.72747707e+01,  1.60951118e+01, -8.77956009e+00,
                          -1.15773792e+01,  8.18862820e+00, -1.79451227e+00,  1.13574104e+01,
                           6.66828251e+00,  9.63613912e-02,  1.04962177e+01,  1.43521202e+00,
                           6.56880236e+00, -2.22902632e+00,  1.79059162e+01, -8.58966541e+00,
                           1.06122971e+01,  8.22393799e+00, -1.81671751e+00, -4.02079964e+00,
                           7.96672440e+00,  8.47757041e-01, -4.45388365e+00, -1.34255123e+00,
                           2.19093537e+00,  6.64698648e+00, -4.34683561e+00, -4.38514280e+00,
                           1.02598095e+01,  1.29314125e+00,  4.80993152e-01,  7.98308659e+00,
                           1.03904562e+01,  7.68913448e-01,  1.63639317e+01, -2.30418706e+00,
                           1.78054821e+00, -2.43359542e+00,  8.70647240e+00,  6.93151903e+00,
                           8.21648979e+00, -1.78727424e+00,  1.60898628e+01,  1.74828374e+00,
                          -2.47949338e+00,  8.17114735e+00, -2.43673921e+00, -8.58457279e+00,
                           1.63362408e+01, -1.69380116e+00,  1.00359793e+01,  2.59160399e-01,
                           6.51342344e+00,  1.13574934e+01, -4.51579189e+00,  1.07076693e+01,
                          -1.15773849e+01, -2.25648832e+00,  7.73517549e-01,  1.69609690e+00,
                          -1.88494265e+00,  7.36989737e-01, -1.79177511e+00,  9.92658234e+00,
                          -4.39313364e+00,  1.71946850e+01,  1.0

In [20]:
topic_model.visualize_heatmap()


ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'coloraxis': 'coloraxis',
              'hovertemplate': 'x: %{x}<br>y: %{y}<br>Similarity Score: %{z}<extra></extra>',
              'name': '0',
              'type': 'heatmap',
              'x': [0_risk_resilience_risks, 1_empathy_victimization_psy...,
                    2_algebras_algebra_schubert, 3_retailers_retail_business,
                    4_lgbtq_transgender_gender, 5_statistical_probability_t...,
                    6_financial_investment_owne..., 7_nursing_teaching_nurse,
                    8_ants_foraging_habitats, 9_benthic_fish_phytoplankton,
                    10_ants_insecticides_insect..., 11_communication_communicat...,
                    12_practitioners_social_art..., 13_economic_income_inequality,
                    14_resilience_burnout_stress, 15_stellar_galactic_galaxies,
                    16_literacies_literacy_read..., 17_ethics_ethical_moral,
                    18_primates_primate_monkeys, 19_economics_economists_con...,
                    20_sociolinguistic_linguist..., 21_metacognitive_comprehens...,
                    22_biology_frog_genetic, 23_arousal_effects_conspeci...,
                    24_predation_animals_monkeys, 25_business_regulators_endo...,
                    26_embodied_pain_consciousn..., 27_bioimpedance_exercise_st...,
                    28_physics_scattering_exper..., 29_executives_executive_str...,
                    30_neurons_myelin_demyelina..., 31_insecurity_intelligence_...,
                    32_entrepreneurship_busines..., 33_postcoloniality_postcolo...,
                    34_cancer_patient_patients, 35_bluebirds_wildlife_chicks,
                    36_geomorphological_geospat..., 37_diplomacy_internationali...,
                    38_muslim_religiosity_adher..., 39_disparities_outcomes_inc...,
                    40_nursing_nurses_nurse, 41_intersectionality_immigr...,
                    42_forests_forested_refores..., 43_schools_reform_reforms,
                    44_lobbying_environmentally..., 45_psychology_psychological...,
                    46_economics_economists_mac..., 47_film_journalism_films,
                    48_investment_entrepreneurs..., 49_victimization_victimized...,
                    50_conservation_iucn_defore..., 51_firms_shareholder_b2b,
                    52_metacognitive_learned_le..., 53_regulations_regulatory_r...,
                    54_pollution_pandemic_morta..., 55_chemistry_ligands_ligand,
                    56_reptiles_endangered_spar..., 57_music_improvisation_cont...,
                    58_climate_flooding_shoreli..., 59_family_internationalizat...,
                    60_memories_philosophizing_..., 61_milky_stellar_abundances,
                    62_turtles_regenerative_reg..., 63_evolution_phylogenetical...,
                    64_privilege_oppression_com..., 65_obesity_health_sleep,
                    66_leadership_commitment_ma..., 67_firms_ecosystem_entrepre...,
                    68_gpa_students_college, 69_leader_leaders_integrity,
                    70_coping_stress_mental, 71_precipitation_rainfall_c...,
                    72_communication_signals_ea..., 73_soils_soil_marshes,
                    74_lidar_multispectral_ecol..., 75_neuroglia_glial_glia,
                    76_mathematics_teacher_teac..., 77_conjecture_matrices_fibo...,
                    78_translanguaging_linguist..., 79_capitalistorganizations_...,
                    80_memristors_memristive_eq..., 81_sustainability_resilienc...,
                    82_obesogen_sulfosuccinate_..., 83_placement_hired_hires,
                    84_salesman_words_wordplay, 85_elephants_elephant_navig...,
                    86_libraries_health_facebook, 87_physics_experiments_expe...,
                    88_preschool_curiosity_scie..., 89_aquaculture_tilapia_fish,
                    90_candidates_candidacy_can..., 91_deforestation_poverty_rica,
                    92_histories_archivist_coll..., 93_motives_evolutionary_beh.